### school accident system

In [1]:
import numpy as np
import pandas as pd

In [2]:
#for view data 
pd.set_option('display.max_rows' , None)
# pd.reset_option('display.max_rows' )
# pd.set_option('display.max_rows' , 1000)
pd.set_option('display.max_rows' , None)

In [3]:
np.random.seed(42)
N=5000

In [4]:
speed =np.random.normal(45,10,N)

In [5]:
#synthetic data
fatigue = np.random.uniform(0,10,N)
traffic = np.random.uniform(0,1,N)
visibility = np.random.normal(600 , 200 ,N)
brakes_event = np.random.poisson(3,N)
school_hours = np.random.randint(5,10,N)
weather = np.random.choice(["clear" ,"Rainy" , "fog"] , size = N , p =[0.6 , 0.25 , 0.15])


In [7]:
speed += np.random.normal(0,5,N)
visibility += np.random.normal(0,50,N)

In [8]:
outliers = np.random.choice(N,50) 
speed[outliers] =np.random.uniform(100,140,50)

In [9]:
type(outliers)

numpy.ndarray

In [10]:
df =pd.DataFrame({
    "speed_Kmph":  speed,
    "fatigue" : fatigue,
    "traffic" :traffic,
    "visibility" : visibility,
    "brakes_event" : brakes_event,
    "school_hours" : school_hours,
    "weather" : weather

})

In [11]:
df

speed_Kmph   fatigue   traffic   visibility  brakes_event  school_hours  \
0      50.046364  1.682366  0.312656   325.074435             3             8   
1      44.254674  1.899347  0.178233   235.017529             7             7   
2      50.754583  4.607122  0.859182    76.331023             2             6   
3      56.223296  2.862799  0.403523   726.153719             7             6   
4      48.301720  2.474630  0.398544   647.346980             0             6   
5      52.111486  6.452376  0.169887   755.736923             3             6   
6      60.687568  6.509717  0.383066   542.475155             6             9   
7      64.352838  8.245171  0.871617   218.889830             2             9   
8      49.887321  4.177086  0.363129   481.729138             1             6   
9      49.698333  0.730851  0.951604   777.722332             2             8   
10     46.882646  2.736664  0.946309   592.494697             6             5   
11     40.094784  9.800055  0.144899   475.308361             3             5   
12     49.514053  5.962586  0.177311   603.347638             2             9   
13     27.073462  7.097371  0.862674   575.072131             6             8   
14     27.614140  0.073578  0.392761   576.713755             3             8   
15     32.029196  5.182057  0.004374   462.544877             1             7   
16     30.311708  0.375287  0.273872   776.227063             3             9   
17     45.062960  5.692302  0.597629   506.474132             4             8   
18     38.372793  9.207708  0.799266   376.062538             5             8   
19     37.149643  9.684191  0.133389   436.517699             5             5   
20     63.771081  5.405527  0.110541   509.987561             1             8   
21     35.435760  4.582048  0.922093   742.542405             2             8   
22     40.802518  9.450171  0.751148   641.075748             7             6   
23     24.896226  6.736098  0.589780   682.142869             3             5   
24     57.555966  0.648993  0.769187   293.697046             3             5   
25    129.815370  4.657256  0.428854   681.204737             2             6   
26     41.506748  2.402450  0.758456   480.401396             2             5   
27     50.793207  4.698043  0.371803   503.246804             2             7   
28     31.429328  4.554656  0.244095   839.767015             4             7   
29     44.116728  5.821448  0.729013   776.437411             6             9   
30     44.038066  3.567705  0.419672   319.233752            10             5   
31     69.022484  1.642704  0.981377   160.781738             3             5   
32     59.779434  5.037194  0.349485   617.052780             3             7   
33     33.731605  8.302029  0.921727   330.482301             2             9   
34     65.555046  6.640122  0.932963   607.859318             2             9   
35     35.553293  3.383679  0.241853   531.540665             6             7   
36     42.941636  9.355230  0.798221   702.952304             1             7   
37     30.484270  9.122076  0.433075   371.054904             4             6   
38     26.302663  2.093484  0.917525  1026.579072             6             9   
39     50.976980  0.394176  0.450124  1128.808875             2             9   
40     58.839737  7.413087  0.744304   646.867154             3             6   
41     47.825656  8.276103  0.466967   535.478167             1             7   
42     48.761344  9.678646  0.227801   618.317657             5             6   
43     44.219495  8.898364  0.199350   600.674689             1             6   
44     28.228893  6.005348  0.425431   341.330006             3             8   
45     37.274209  5.300523  0.755495   451.020631             3             9   
46     43.547435  0.278411  0.605071   374.816137             4             7   
47     62.355643  2.466564  0.688629   611.029521             2             8   
48     46.019388  4.596148  0.282326 

# Feature engineering 

In [12]:
df['overspeeding'] =(df["speed_Kmph"] > 50).astype(int)

In [13]:
df["traffic"] = df ["traffic"]*df["speed_Kmph"]
df["visibility_risk"] = 1/(df["visibility"]+1)
df["rush_hours"] = df["school_hours"].isin([8,9,10,16,17,18]).astype(int)
df["fatigue_speed_risk"] = df["speed_Kmph"] * df["fatigue"]
df["harsh_brake"] = (df["brakes_event"]>8).astype(int)
weather_risk = {"clear":1 , "rain":1.5 , "fog":2}
df["weather_risk"] = df["weather"].map(weather_risk)

In [14]:
risk_score =(
    0.3 *df["speed_Kmph"]+
    0.25*df["fatigue_speed_risk"]+
    0.2 *df["traffic"]+
    0.15 *df["visibility_risk"]+
    0.1 *df["harsh_brake"]
    
)

In [15]:
prob = 1/ (1 + np.exp(-risk_score))
df["accident_risk"] =(prob>0.5) .astype(int)
print(df)

      speed_Kmph   fatigue     traffic   visibility  brakes_event  \
0      50.046364  1.682366   15.647312   325.074435             3   
1      44.254674  1.899347    7.887648   235.017529             7   
2      50.754583  4.607122   43.607435    76.331023             2   
3      56.223296  2.862799   22.687380   726.153719             7   
4      48.301720  2.474630   19.250347   647.346980             0   
5      52.111486  6.452376    8.853047   755.736923             3   
6      60.687568  6.509717   23.247324   542.475155             6   
7      64.352838  8.245171   56.091018   218.889830             2   
8      49.887321  4.177086   18.115519   481.729138             1   
9      49.698333  0.730851   47.293111   777.722332             2   
10     46.882646  2.736664   44.365465   592.494697             6   
11     40.094784  9.800055    5.809680   475.308361             3   
12     49.514053  5.962586    8.779399   603.347638             2   
13     27.073462  7.097371   23.35

In [113]:
df.to_csv("school_bus_modelworkshop.csv",index=False)

In [97]:
df

speed_Kmph   fatigue     traffic   visibility  brakes_event  \
0      49.510795  1.682366   15.479863   340.984142             3   
1      49.684210  1.899347    8.855371   307.995501             7   
2      48.821424  4.607122   41.946499   135.919374             2   
3      60.500025  2.862799   24.413137   780.631162             7   
4      46.012673  2.474630   18.338061   727.933213             0   
5      43.743830  6.452376    7.431494   759.911420             3   
6      62.247987  6.509717   23.845067   623.430454             6   
7      53.927032  8.245171   47.003710   203.675312             2   
8      46.821990  4.177086   17.002409   490.752030             1   
9      50.914066  0.730851   48.450006   698.877026             2   
10     37.397682  2.736664   35.389759   578.876944             6   
11    121.432339  9.800055   17.595383   531.657393             3   
12     53.884036  5.962586    9.554246   671.182632             2   
13     30.150099  7.097371   26.009708   500.244434             6   
14     27.217255  0.073578   10.689874   621.461000             3   
15     35.494794  5.182057    0.155254   495.997607             1   
16     32.115517  0.375287    8.795535   795.573495             3   
17     48.070623  5.692302   28.728398   508.951111             4   
18     35.505245  9.207708   28.378134   301.019645             5   
19     27.230378  9.684191    3.632222   428.416371             5   
20     64.409365  5.405527    7.119899   506.502590             1   
21     39.902582  4.582048   36.793878   746.809190             2   
22     41.158277  9.450171   30.915973   637.881322             7   
23     29.766092  6.736098   17.555434   641.679521             3   
24     41.884376  0.648993   32.216909   319.601702             3   
25     41.517572  4.657256   17.804992   706.374991             2   
26     33.741247  2.402450   25.591243   431.777030             2   
27     46.588265  4.698043   17.321656   531.179168             2   
28     37.359096  4.554656    9.119153   872.426892             4   
29     42.035692  5.821448   30.644584   715.029365             6   
30     41.943281  3.567705   17.602433   334.446357            10   
31     63.570870  1.642704   62.386996   166.616970             3   
32     57.962212  5.037194   20.256934   634.421415             3   
33     37.872507  8.302029   34.908128   357.282467             2   
34     55.262400  6.640122   51.557749   623.317039             2   
35     31.275728  3.383679    7.564127   545.508037             6   
36     44.561394  9.355230   35.569849   658.411645             1   
37     30.455432  9.122076   13.189471   415.776948             4   
38     23.786938  2.093484   21.825104   928.896777             6   
39     52.589616  0.394176   23.671863  1162.066289             2   
40     58.197614  7.413087   43.316700   603.412114             3   
41     46.121264  8.276103   21.537127   606.832169             1   
42     49.618523  9.678646   11.303137   651.641816             5   
43     40.554766  8.898364    8.084598   611.726981             1   
44     29.752286  6.005348   12.657551   384.716347             3   
45     40.345374  5.300523   30.480714   422.063574             3   
46     38.541160  0.278411   23.320157   346.635374             4   
47     59.139082  2.466564   40.724904   646.440839             2   
48     46.113428  4.596148   13.019036   479.532414             2   
49     28.747045  6.285039   13.839844    95.794766             4   
50     61.430981  5.572518    2.727245   651.627702             0   
51     43.552404  7.426360   35.605502   638.118508             3   
52     43.664281  2.797669   43.222929   847.561125             3   
53     55.678158  5.649526   22.654277   572.818681             7   
54     45.398633  0.881422    0.497735   300.673991             3   
55     53.845739  4.136655    9.142610    90.110302             2   
56     43.461348  7.501608   28.359698   442.986970             2   
57  